In [1]:
import plotly.graph_objects as go
import plotly
from plotly.subplots import make_subplots
import pandas as pd
import urllib.request
import os
import re
import glob
import datetime
import dateutil.relativedelta
import numpy as np
from ipywidgets import widgets

from IPython.display import display

import matplotlib.pyplot as plt

In [18]:
def row_sum(arow):
    i = 0
    for x in arow:
        if type(arow[x]) == float:
            i+=arow[x]
    return i


def refresh_data():

    
    url = 'https://github.com/CSSEGISandData/COVID-19/tree/master/csse_covid_19_data/csse_covid_19_daily_reports'
    response = urllib.request.urlopen(url)
    data = response.read()      # a `bytes` object
    text = data.decode('utf-8') # a `str`; this step can't be used if data is binary

    [os.system('rm {}'.format(i)) for i in glob.glob("daily_data/*csv*")]

    for x in set(re.findall("[0-9]+\-[0-9]+\-20[0-9]+", text)):
        os.system("wget https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/{}.csv  -P daily_data/".format(x))
        
    data_files = glob.glob('daily_data/*.csv')
    
    summaries = []
    deaths = []
    
    for entry in data_files:
        temp = {}
        death = {}
        x = pd.read_csv(entry)
        date = (entry.split('/')[1].split('.')[0]).split('-')
        date =  datetime.datetime.fromisoformat("-".join([date[2],date[0], date[1]]))
        x['date'] = date
        temp['date'] = date
        death['date'] = date
        
        # country coding varies as of 3-11-2020
        
        x['Country/Region'] = x['Country/Region'].apply(lambda i: "Iran" if "Iran" in i else i)
        x['Country/Region'] = x['Country/Region'].apply(lambda i: "South Korea" if "Republic of Korea" == i else i)
        
        for country in x['Country/Region'].unique():
            temp[country] = sum( x[x['Country/Region']==country]['Confirmed'])
            death[country] = sum(x[x['Country/Region']==country]['Deaths'])
        deaths.append(death)
        summaries.append(temp)

    death_table = pd.DataFrame(deaths).sort_values(by="date").fillna(0)
    summary_table = pd.DataFrame(summaries).sort_values(by="date").fillna(0)


    return death_table, summary_table


In [19]:
death_table, summary_table = refresh_data()

In [20]:
death_table['global'] = death_table.apply(lambda x: sum([i for i in x if type(i) == float]), axis=1)
summary_table['global'] = summary_table.apply(lambda x: sum([i for i in x if type(i) == float]), axis=1)

all_countries = ['global'] + sorted([i for i in death_table.columns if i not in ["date", 'global']])
col_entry = summary_table.tail(1).T.columns[0]
all_countries = summary_table[all_countries].tail(1).T.sort_values(by=col_entry, ascending=False).index.to_list()

In [21]:
# Create figure
fig = make_subplots(rows=2, cols=2, shared_xaxes=True, subplot_titles=["","South Korea - Linear","", "South Korea - Log"])


n_traces = 12

# Add surface trace
for country in all_countries:
    if country == 'global':
        viz = True
    else:
        viz = False
        
    ## core scatter lots
    
    fig.add_trace(go.Scatter(
        x=death_table["date"], y=death_table[country],
        name='death', visible=viz, line=dict(color="#3498DB"),
        mode='lines+markers', showlegend=False),
        row=1, col=1
    )

    fig.add_trace(go.Scatter(
        x=summary_table["date"], y=summary_table[country],
        name='confirmed', visible=viz, line=dict(color="#FF0000"),
        mode='lines+markers', showlegend=False),
        row=1, col=1
    )

    fig.add_trace(go.Scatter(
        x=death_table["date"], y=np.log10(death_table[country]),
        name='log10 death - {}'.format(country), visible=viz, line=dict(color="#3498DB"),
        mode='lines+markers', showlegend=False),
        row=2, col=1
    )

    fig.add_trace(go.Scatter(
        x=summary_table["date"], y=np.log10(summary_table[country]),
        name='log10 confirmed - {}'.format(country), visible=viz, line=dict(color="#FF0000"),
        mode='lines+markers', showlegend=False),
        row=2, col=1
    )
    
    ## additional analysis
    
    x_min = min(summary_table['date'])
    x_max = max(summary_table['date'])
        
    pct_05 = max(summary_table[country]) * 0.005
    pct_1 = max(summary_table[country]) * 0.01
    pct_3 = max(summary_table[country]) * 0.03
    pct_5 = max(summary_table[country]) * 0.05
    
    
    for pct, h_color, val in zip([pct_05, pct_1, pct_3, pct_5], 
                                 ["#D2B4DE", "#AED6F1", "#ABEBC6", "#F9E79F"],
                                 ['0.05%', '1%', '3%', '5%']
                                ):
        
        fig.add_trace(go.Scatter(x=[x_min, x_max], y=[pct, pct],
                                 mode='lines', name=val,  visible=viz, 
                                 line=dict(color=h_color, width=3), showlegend=False), row=1, col=1)
        
        fig.add_trace(go.Scatter(x=[x_min, x_max], y=[np.log10(pct), np.log10(pct)],
                                 mode='lines', name=val,  visible=viz, 
                                 line=dict(color=h_color, width=3), showlegend=False), row=2, col=1)

fig.add_trace(go.Scatter(
    x=death_table["date"], y=death_table["South Korea"],
    name='death', visible=True, line=dict(color="#3498DB"),
    mode='lines+markers', showlegend=True),
    row=1, col=2
)

fig.add_trace(go.Scatter(
    x=summary_table["date"], y=summary_table["South Korea"],
    name='confirmed', visible=True, line=dict(color="#FF0000"),
    mode='lines+markers', showlegend=True),
    row=1, col=2
)

fig.add_trace(go.Scatter(
    x=death_table["date"], y=np.log10(death_table["South Korea"]),
    name='log10 death - SK', visible=True, line=dict(color="#3498DB"),
    mode='lines+markers', showlegend=False),
    row=2, col=2
)

fig.add_trace(go.Scatter(
    x=summary_table["date"], y=np.log10(summary_table["South Korea"]),
    name='log10 confirmed - SK', visible=True, line=dict(color="#FF0000"),
    mode='lines+markers', showlegend=False),
    row=2, col=2
)

## additional analysis - sk Specific    
pct_05 = max(summary_table["South Korea"]) * 0.005
pct_1 = max(summary_table["South Korea"]) * 0.01
pct_3 = max(summary_table["South Korea"]) * 0.03
pct_5 = max(summary_table["South Korea"]) * 0.05


for pct, h_color, val in zip([pct_05, pct_1, pct_3, pct_5], 
                             ["#D2B4DE", "#AED6F1", "#ABEBC6", "#F9E79F"],
                             ['0.5%', '1%', '3%', '5%']
                            ):

    fig.add_trace(go.Scatter(x=[x_min, x_max], y=[pct, pct],
                             mode='lines', name=val,  visible=True, 
                             line=dict(color=h_color, width=3), showlegend=True), row=1, col=2)

    fig.add_trace(go.Scatter(x=[x_min, x_max], y=[np.log10(pct), np.log10(pct)],
                             mode='lines', name=val,  visible=True, 
                             line=dict(color=h_color, width=3), showlegend=False), row=2, col=2)


# Update plot sizing
fig.update_layout(
    width=800,
    height=900,
    autosize=False,
    margin=dict(t=100, b=0, l=0, r=0),
    title_text="Global vs South Korea"
)

fig.update_yaxes(title_text="Linear infected and deceased", row=1, col=1)
fig.update_yaxes(title_text="Log10 infected and deceased", row=2, col=1)


fig.update_layout(
    updatemenus=[
        dict(
            buttons=[
                dict(
                    args=[{"visible": [i==x for i in all_countries for _ in range(n_traces)] + [True] * n_traces},
                          {"title": "{} vs South Korea".format(x)},
                          {"subplot_titles": [x, "", "SK", ""]}
                         ],
                    label=x,
                    method="update",
                   # country=x
                    
                ) for x in all_countries
            ],
            direction="down",
            pad={"r": 10, "t": 10},
            showactive=True,
            x=0,
            xanchor="left",
            y=1.2,
            yanchor="top"
        ),
    ]
)


fig.show()

/opt/anaconda3/lib/python3.7/site-packages/pandas/core/series.py:853: RuntimeWarning:

divide by zero encountered in log10



In [ ]:
plotly.offline.plot(fig, filename = 'test-covid.html', auto_open=False)

In [17]:
summary_table

date  Mainland China  South Korea  Others    Italy  Japan    Iran  \
28 2020-01-22             0.0          1.0     0.0      0.0    2.0     0.0   
29 2020-01-23             0.0          1.0     0.0      0.0    1.0     0.0   
39 2020-01-24             0.0          2.0     0.0      0.0    2.0     0.0   
38 2020-01-25          1399.0          2.0     0.0      0.0    2.0     0.0   
22 2020-01-26          2062.0          3.0     0.0      0.0    4.0     0.0   
23 2020-01-27          2863.0          4.0     0.0      0.0    4.0     0.0   
34 2020-01-28          5494.0          4.0     0.0      0.0    7.0     0.0   
35 2020-01-29          6070.0          4.0     0.0      0.0    7.0     0.0   
17 2020-01-30          8124.0          4.0     0.0      0.0   11.0     0.0   
16 2020-01-31          9783.0         11.0     0.0      2.0   15.0     0.0   
46 2020-02-01         11871.0         12.0     0.0      2.0   20.0     0.0   
14 2020-02-02         16607.0         15.0     0.0      2.0   20.0     0.0   
15 2020-02-03         19693.0         15.0     0.0      2.0   20.0     0.0   
10 2020-02-04         23680.0         16.0     0.0      2.0   22.0     0.0   
9  2020-02-05         27409.0         19.0     0.0      2.0   22.0     0.0   
26 2020-02-06         30553.0         23.0     0.0      2.0   45.0     0.0   
27 2020-02-07         34075.0         24.0    61.0      3.0   25.0     0.0   
11 2020-02-08         36778.0         24.0    61.0      3.0   25.0     0.0   
12 2020-02-09         39790.0         25.0    64.0      3.0   26.0     0.0   
31 2020-02-10         42306.0         27.0   135.0      3.0   26.0     0.0   
30 2020-02-11         44327.0         28.0   135.0      3.0   26.0     0.0   
5  2020-02-12         44699.0         28.0   175.0      3.0   28.0     0.0   
6  2020-02-13         59832.0         28.0   175.0      3.0   28.0     0.0   
21 2020-02-14         66292.0         28.0   218.0      3.0   29.0     0.0   
20 2020-02-15         68347.0         28.0   285.0      3.0   43.0     0.0   
40 2020-02-16         70446.0         29.0   355.0      3.0   59.0     0.0   
41 2020-02-17         72364.0         30.0   454.0      3.0   66.0     0.0   
2  2020-02-18         74139.0         31.0   542.0      3.0   74.0     0.0   
3  2020-02-19         74546.0         31.0   621.0      3.0   84.0     2.0   
19 2020-02-20         74999.0        104.0   634.0      3.0   94.0     5.0   
18 2020-02-21         75472.0        204.0   634.0     20.0  105.0    18.0   
42 2020-02-22         76922.0        433.0   634.0     62.0  122.0    28.0   
43 2020-02-23         76938.0        602.0   691.0    155.0  147.0    43.0   
33 2020-02-24         77152.0        833.0   691.0    229.0  159.0    61.0   
32 2020-02-25         77660.0        977.0   691.0    322.0  170.0    95.0   
0  2020-02-26         78065.0       1261.0   705.0    453.0  189.0   139.0   
1  2020-02-27         78498.0       1766.0   705.0    655.0  214.0   245.0   
36 2020-02-28         78824.0       2337.0   705.0    888.0  228.0   388.0   
37 2020-02-29         79251.0       3150.0   705.0   1128.0  241.0   593.0   
13 2020-03-01         79826.0       3736.0   705.0   1694.0  256.0   978.0   
45 2020-03-02         80026.0       4335.0   705.0   2036.0  274.0  1501.0   
44 2020-03-03         80151.0       5186.0   706.0   2502.0  293.0  2336.0   
24 2020-03-04         80271.0       5621.0   706.0   3089.0  331.0  2922.0   
25 2020-03-05         80422.0       6088.0   706.0   3858.0  360.0  3513.0   
8  2020-03-06         80573.0       6593.0   696.0   4636.0  420.0  4747.0   
7  2020-03-07         80652.0       7041.0   696.0   5883.0  461.0  5823.0   
48 2020-03-08         80699.0       7314.0   696.0   7375.0  502.0  6566.0   
47 2020-03-09         80735.0       7478.0   696.0   9172.0  511.0  7161.0   
4  2020-03-10         80757.0          0.0   696.0  10149.0  581.0     0.0   

    Singapore  Hong Kong     US  ...  Ukraine  Palestine  Vatican City  \
28        0.0        0.0    1.0  .